In [5]:
!curl -O "https://raw.githubusercontent.com/amephraim/nlp/master/texts/J.%20K.%20Rowling%20-%20Harry%20Potter%201%20-%20Sorcerer's%20Stone.txt"
!curl https://raw.githubusercontent.com/amephraim/nlp/master/texts/J.%20K.%20Rowling%20-%20Harry%20Potter%202%20-%20The%20Chamber%20Of%20Secrets.txt
!curl https://raw.githubusercontent.com/amephraim/nlp/master/texts/J.%20K.%20Rowling%20-%20Harry%20Potter%203%20-%20Prisoner%20of%20Azkaban.txt
!curl https://raw.githubusercontent.com/amephraim/nlp/master/texts/J.%20K.%20Rowling%20-%20Harry%20Potter%204%20-%20The%20Goblet%20of%20Fire.txt
!curl https://raw.githubusercontent.com/bobdeng/owlreader/master/ERead/assets/books/Harry%20Potter%20and%20the%20Order%20of%20the%20Phoenix.txt
!curl https://raw.githubusercontent.com/bobdeng/owlreader/master/ERead/assets/books/Harry%20Potter%20and%20The%20Half-Blood%20Prince.txt
!curl https://raw.githubusercontent.com/bobdeng/owlreader/master/ERead/assets/books/Harry%20Potter%20and%20the%20Deathly%20Hallows%20.txt

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  429k  100  429k    0     0  3485k      0 --:--:-- --:--:-- --:--:-- 3702k

HARRY POTTER AND THE CHAMBER OF SECRETS
by J. K. Rowling

(this is BOOK 2 in the Harry Potter series)

Original Scanned/OCR: Friday, April 07, 2000
v1.0
(edit where needed, change version number by 0.1)


C H A P T E RR		O N E

THE WORST BIRTHDAY

Not for the first time, an argument had broken out over breakfast at
number four, Privet Drive. Mr. Vernon Dursley had been woken in
the early hours of the morning by a loud, hooting noise from his
nephew Harry's room.

"Third time this week!" he roared across the table. "If you can't
control that owl, it'll have to go!"

Harry tried, yet again, to explain.

"She's bored," he said. "She's used to flying around outside. If I could
just let her out at night -"

"Do I look stupid?" snarled Uncle Vernon, a bit of

Start by reading some sample text

In [7]:
with open('input1.txt') as f:
    text = f.read()
print(text[:100])

Harry Potter and the Sorcerer's Stone


CHAPTER ONE

THE BOY WHO LIVED

Mr. and Mrs. Dursley, of num


In [4]:
filenames = ["J. K. Rowling - Harry Potter 1 - Sorcerer's Stone.txt", "J. K. Rowling - Harry Potter 2 - The Chamber Of Secrets.txt", "J. K. Rowling - Harry Potter 3 - Prisoner of Azkaban.txt", "J. K. Rowling - Harry Potter 4 - The Goblet of Fire.txt", "Harry Potter and the Order of the Phoenix.txt", "Harry Potter and The Half-Blood Prince.txt", "Harry Potter and the Deathly Hallows .txt"]
text = ''
for file in filenames:
  with open(file, 'r', encoding='utf-8', errors='replace') as f:
    text += f.read()
print(len(text))
print(text[:1000])

FileNotFoundError: [Errno 2] No such file or directory: "J. K. Rowling - Harry Potter 1 - Sorcerer's Stone.txt"

Define our list of possible characters - the "vocabulary" of our GPT. The GPT will be able to generate from this list of characters.

In [8]:
chars = sorted(list(set(text)))
vocab_size = len(chars)
print(''.join(chars))
print(vocab_size)

	
 !"'()*,-.0123456789:;?ABCDEFGHIJKLMNOPQRSTUVWXYZ\abcdefghijklmnopqrstuvwxyz~
79


Map our characters to integers for our GPT to parse, and we define some functions to encode our characters to a string, and decode them from an integer.

In [9]:
stoi = {ch:i for i , ch in enumerate(chars)} # string to integer map
itos = {i:ch for i, ch in enumerate(chars)} # integer to string map
encode = lambda s: [stoi[c] for c in s]
decode = lambda l: ''.join([itos[i] for i in l])
print('Encoded string:', encode('hello world'))
print('Decoded string:', decode(encode('hello world')))

Encoded string: [59, 56, 63, 63, 66, 2, 74, 66, 69, 63, 55]
Decoded string: hello world


We now encode our data using the previously defined map.

In [11]:
import torch
device = 'mps' if torch.backends.mps.is_available() else 'cpu'
data = torch.tensor(encode(text), dtype=torch.long, device=device)
print(data.shape, data.dtype)
print(data[:100])

torch.Size([439742]) torch.int64
tensor([32, 52, 69, 69, 76,  2, 40, 66, 71, 71, 56, 69,  2, 52, 65, 55,  2, 71,
        59, 56,  2, 43, 66, 69, 54, 56, 69, 56, 69,  5, 70,  2, 43, 71, 66, 65,
        56,  1,  1,  1, 27, 32, 25, 40, 44, 29, 42,  2, 39, 38, 29,  1,  1, 44,
        32, 29,  2, 26, 39, 49,  2, 47, 32, 39,  2, 36, 33, 46, 29, 28,  1,  1,
        37, 69, 11,  2, 52, 65, 55,  2, 37, 69, 70, 11,  2, 28, 72, 69, 70, 63,
        56, 76,  9,  2, 66, 57,  2, 65, 72, 64], device='mps:0')


We split our data into a training and testing set - 90% for training and the rest for testing.

In [12]:
n = int(0.9 * len(data))
train_data = data[:n]
test_data = data[n:]

The block size represents the context length - how many characters the model will consider before predicting the next character. Eg. setting the block size to 8 means the model will consider up to 8 characters prior to the last one to predict the next character.

In [13]:
block_size = 64
train_data[:block_size + 1]

tensor([32, 52, 69, 69, 76,  2, 40, 66, 71, 71, 56, 69,  2, 52, 65, 55,  2, 71,
        59, 56,  2, 43, 66, 69, 54, 56, 69, 56, 69,  5, 70,  2, 43, 71, 66, 65,
        56,  1,  1,  1, 27, 32, 25, 40, 44, 29, 42,  2, 39, 38, 29,  1,  1, 44,
        32, 29,  2, 26, 39, 49,  2, 47, 32, 39,  2], device='mps:0')

We obtain the training data for the model. Based on our block size (context length), we obtain batches of training data. Each batch is randomly generated from some start position in our text. The batch will consist of the input characters to the model, and the correct target outputs that we would like our model to predict. That is, the next character in the sequence

In [16]:
batch_size = 16

def get_batch(split):
  data = train_data if split == 'train' else test_data

  batches_start_pos = torch.randint(len(data) - block_size, (batch_size,)) # four randints for start pos

  inputs = torch.stack([data[i:i + block_size] for i in batches_start_pos]) # context chars
  targets = torch.stack([data[i + 1:i + block_size + 1] for i in batches_start_pos]) # target chars

  inputs, targets = inputs.to(device), targets.to(device)

  return inputs, targets

input_batch, target_batch = get_batch('train')
print('inputs:')
print(input_batch.shape)
print(input_batch)
print('targets:')
print(target_batch.shape)
print(target_batch)

for b in range(batch_size):
  for t in range(block_size):
    context = input_batch[b, :t+1]
    target = target_batch[b,t]


inputs:
torch.Size([16, 64])
tensor([[66, 64,  2,  ...,  2,  4, 43],
        [63,  2, 10,  ..., 58, 56,  9],
        [53, 60, 62,  ..., 66, 69, 56],
        ...,
        [74, 52, 70,  ..., 70, 66, 72],
        [ 2, 72, 70,  ..., 72, 67,  2],
        [56, 55,  2,  ...,  2, 38, 56]], device='mps:0')
targets:
torch.Size([16, 64])
tensor([[64,  2, 70,  ...,  4, 43, 56],
        [ 2, 10, 10,  ..., 56,  9,  2],
        [60, 62, 56,  ..., 69, 56,  9],
        ...,
        [52, 70,  2,  ..., 66, 72, 65],
        [72, 70, 56,  ..., 67,  2, 10],
        [55,  2, 53,  ..., 38, 56, 73]], device='mps:0')


In [17]:
import torch.nn as nn
from torch.nn import functional as F

In [18]:
# hyperparams
n_embd = 128 # dimension of each vector for each token - how many data points we want to assign to each token
n_head = 4
n_layer = 4
dropout = 0.0 # percent of nodes dropped by dropout layer

In [19]:
class AttentionHead(nn.Module):
  """Defines a single head of self-attention."""

  def __init__(self, head_size):
    super().__init__()
    self.key = nn.Linear(n_embd, head_size, bias=False)
    self.query = nn.Linear(n_embd, head_size, bias=False)
    self.value = nn.Linear(n_embd, head_size, bias=False)

    # defines a triangular matrix to mask out values that we don't want in training - see readme for details
    self.register_buffer('tril_mask', torch.tril(torch.ones(block_size, block_size)))

    self.dropout = nn.Dropout(dropout)

  def forward(self, x):
    """Accepts an input tensor of dim batch_size * block_size * channels
    Outputs to a tensor of dim batch_size * block_size * head_size"""
    batch, time, channel = x.shape

    # generating key and query vectors for each token
    keys = self.key(x) # dim = (batch, time, head_size)
    queries = self.query(x) # dim = (batch, time, head_size)
    # associate keys and queries to find values with high correlation via matrix mul
    # an additional sqrt term is introduced to decrease variance for softmax - see readme for details
    weights = queries @ keys.transpose(-2, -1) * keys.shape[-1] ** 0.5
    # masks weight values using the previously defined matrix, replaces 0 values with -inf in prep for softmax
    weights = weights.masked_fill(self.tril_mask[:time, :time] == 0, float('-inf'))
    # softmax to convert to normalized probabilities
    weights = F.softmax(weights, dim=-1)

    weights = self.dropout(weights)

    values = self.value(x)

    return weights @ values


In [20]:
class MultiheadAttention(nn.Module):

  def __init__(self, num_heads, head_size):
    super().__init__()
    self.heads = nn.ModuleList([AttentionHead(head_size) for _ in range(num_heads)])
    self.proj = nn.Linear(head_size * num_heads, n_embd) # projects back to number of embeddings
    self.dropout = nn.Dropout(dropout)

  def forward(self, x):
    out = torch.cat([head(x) for head in self.heads], dim=-1)
    return self.dropout(self.proj(out))



In [21]:
class FeedForward(nn.Module):
  """Multilayer perceptron in between attention blocks."""

  def __init__(self, n_embd):
    super().__init__()
    self.net = nn.Sequential(
        nn.Linear(n_embd, 4 * n_embd), # based on paper
        nn.ReLU(),
        nn.Linear(4 * n_embd, n_embd),
        nn.Dropout(dropout)
    )

  def forward(self, x):
    return self.net(x)

In [22]:
class Block(nn.Module):

  def __init__(self, n_embd, num_heads):
    super().__init__()
    head_size = n_embd // num_heads
    self.sa = MultiheadAttention(num_heads, head_size) # self attention layer
    self.ffwd = FeedForward(n_embd) # feed forwad nn layer
    self.ln1 = nn.LayerNorm(n_embd)
    self.ln2 = nn.LayerNorm(n_embd)

  def forward(self, x):
    x = x + self.sa(self.ln1(x))
    x = x + self.ffwd(self.ln2(x))
    return x


In [25]:
class GPT(nn.Module):

  def __init__(self):
    super().__init__()
    self.token_embedding_table = nn.Embedding(vocab_size, n_embd, device=device) # creates a vocab_size * n_embd matrix containing vector representation of each token
    self.position_embedding_table = nn.Embedding(block_size, n_embd) # creates a block_size * n_embd matrix embedding each position in the block
    self.blocks = nn.Sequential(*[Block(n_embd, n_head) for _ in range(n_layer)])
    self.ln_f = nn.LayerNorm(n_embd)
    self.final = nn.Linear(n_embd, vocab_size)

    self.apply(self._init_weights)

  def _init_weights(self, module):
    if isinstance(module, nn.Linear):
      torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
      if module.bias is not None:
          torch.nn.init.zeros_(module.bias)
    elif isinstance(module, nn.Embedding):
        torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)

  def forward(self, idx, targets=None):
    batch, time = idx.shape
    # idx and targets are batch_size * block_size tensors of ints
    # passing these through the embedding table gives the vector equivalents with n_embd number of dimensions
    tok_emb = self.token_embedding_table(idx) # unnormalized logits (vector values) for each token
    pos_emb = self.position_embedding_table(torch.arange(time, device=device))
    x = tok_emb + pos_emb
    x = self.blocks(x)
    x = self.ln_f(x)
    logits = self.final(x)

    if targets is None:
      loss = None
    else:
      batch, time, channel = logits.shape # tensor of ints: batch, time (position), channel (token)
      logits = logits.view(batch * time, channel)
      targets = targets.view(batch * time)
      print(logits)
      print(targets)
      loss = F.cross_entropy(logits, targets)

    return logits, loss

  def generate(self, idx, max_new_tokens):
    for _ in range(max_new_tokens):
      idx_cond = idx[:, -block_size:]

      logits, loss = self(idx_cond) # loss is not needed here

      logits = logits[:, -1, :] # last element in time dim

      probs = F.softmax(logits, dim=-1) # normalize probs

      idx_next = torch.multinomial(probs, num_samples=1) # sample from dist

      idx = torch.cat((idx, idx_next), dim=1) # append to result

    return idx



In [26]:
model = GPT()
model = model.to(device)
logits, loss = model(input_batch, target_batch)
print(logits.shape)
print(loss)

idx = torch.zeros((1, 1), dtype=torch.long, device=device) # single input char
print(decode(model.generate(idx, max_new_tokens=200)[0].tolist()))

tensor([[-0.0127, -0.0925,  0.3239,  ..., -0.0076,  0.0417, -0.0294],
        [ 0.0784, -0.0727,  0.3854,  ...,  0.0474,  0.0338, -0.1250],
        [ 0.1139,  0.0779,  0.1437,  ...,  0.3482, -0.2880, -0.0994],
        ...,
        [-0.0729, -0.2730,  0.3747,  ..., -0.1625,  0.2564, -0.1898],
        [ 0.4401, -0.2962,  0.3141,  ...,  0.1135, -0.2331,  0.0707],
        [-0.0876, -0.1851,  0.3952,  ..., -0.3262,  0.0217,  0.0340]],
       device='mps:0', grad_fn=<ViewBackward0>)
tensor([64,  2, 70,  ..., 38, 56, 73], device='mps:0')
torch.Size([1024, 79])
tensor(4.3681, device='mps:0', grad_fn=<NllLossBackward0>)
	?e?hLy-.g2 HyMKAiChnwd23JhSC	imRgf.; RZYmxCtE,khA,:kLwM305NKrTijAJvPTC~(52Mp?
MKc7EAZrRb!?FzG(MZ75	yUM,yBDE1aQ0eu:fS9NL~5Zp1 .kir-!2Kr ,GdmHI	8k!k!!HJ,j	7T;G?SYEc?Lu6kb(H0Y3UdJtd-umur55	WsTWfusHs3	CX(


In [29]:
logits = torch.tensor([[0, 0, 0.7, 0]])
target = torch.tensor([0])
F.cross_entropy(logits, target)

tensor(1.6122)

In [26]:
optimizer = torch.optim.AdamW(model.parameters(), lr=3e-4)
eval_iters = 200


In [21]:
@torch.no_grad()
def estimate_loss():
    out = {}
    model.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(eval_iters)
        for k in range(eval_iters):
            X, Y = get_batch(split)
            logits, loss = model(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean()
    model.train()
    return out

In [31]:
max_iters = 2500

In [32]:
for iter in range(max_iters):
  if iter % 100 == 0 or iter == max_iters - 1:
    losses = estimate_loss()
    print(f"step {iter}: train loss {losses['train']:.4f}, val loss {losses['val']:.4f}")

  inputs, targets = get_batch('train')

  logits, loss = model(inputs, targets)
  optimizer.zero_grad(set_to_none=True)
  loss.backward()
  optimizer.step()

step 0: train loss 1.5406, val loss 1.6193
step 100: train loss 1.5385, val loss 1.6027
step 200: train loss 1.5354, val loss 1.5987
step 300: train loss 1.5187, val loss 1.5984
step 400: train loss 1.5127, val loss 1.5905
step 500: train loss 1.5114, val loss 1.5881
step 600: train loss 1.5117, val loss 1.5749
step 700: train loss 1.4961, val loss 1.5659
step 800: train loss 1.4918, val loss 1.5694
step 900: train loss 1.4964, val loss 1.5609
step 1000: train loss 1.4845, val loss 1.5457
step 1100: train loss 1.4778, val loss 1.5458
step 1200: train loss 1.4703, val loss 1.5380
step 1300: train loss 1.4607, val loss 1.5377
step 1400: train loss 1.4552, val loss 1.5336
step 1500: train loss 1.4646, val loss 1.5329
step 1600: train loss 1.4568, val loss 1.5275
step 1700: train loss 1.4551, val loss 1.5288
step 1800: train loss 1.4466, val loss 1.5171
step 1900: train loss 1.4384, val loss 1.5178
step 2000: train loss 1.4366, val loss 1.5118
step 2100: train loss 1.4328, val loss 1.5160


In [ ]:
losses = estimate_loss()
print(f"step {iter}: train loss {losses['train']:.4f}, val loss {losses['val']:.4f}")

In [33]:
print(decode(model.generate(torch.zeros((1, 1), dtype=torch.long, device=device), max_new_tokens=1000)[0].tolist()))

	as visiteed.
"The light," said Harry, “everything them across the seation listend, 'Harry, wh—' said Harry as though nost the Snighteeling Prophaperable than trying. "No' to to be suking 
disn't going. "I don' me me-t's entered beard's fast with to exame at the cist silner, as this examily appression incide the pair, ludst's armin-do they good over in the way of Mr. Everyone instily hearing. "We they dad-one emerged met the girls wizards of a door, and they night 
was. 

 He neughouldeed highly carm
passide to changes, examising at the Kark as he got headed armcy. 'Ge Mrix Oute of thly beanous at your fadstion was made, who would mean's eyes, did he any where as people bare have to the corrected up even that he called leady, bithrowing, by he couldn't knew armist in its pairs of Mr.
"I -- Prophapear thing!"
Harry leasted deadedly to tiously. Hifted her Expiemaze, looking very
passils.
    'E… I'll be sit opened this
Cup lit up?' said Hermione did do the scarlet wizards. 'I'd say need 